In [1]:
import pandas as pd
import altair as alt
import matplotlib.pyplot as plt
import seaborn as sn


In [2]:
data = pd.read_csv("data/FinalDataset.csv")
data.head()

Unnamed: 0              name  player_height  player_weight  \
0        2912     Devean George         203.20      106.59412   
1        2913       Devin Brown         195.58       95.25432   
2        2914      Devin Harris         190.50       83.91452   
3        2916     Dirk Nowitzki         213.36      111.13004   
4        2918  Donyell Marshall         205.74      111.13004   

             college  country draft_year draft_round draft_number  net_rating  \
0           Augsburg      USA       1999           1           23         0.2   
1  Texas-San Antonio      USA  Undrafted   Undrafted    Undrafted        -0.7   
2          Wisconsin      USA       2004           1            5         5.4   
3               None  Germany       1998           1            9         9.1   
4        Connecticut      USA       1994           1            4       -14.6   

   ...  FG% by Distance 16-3P  FG% by Distance 3P  2P FG AST%  3P FG AST%  \
0  ...                  0.308            0.324000    0.596000       0.955   
1  ...                  0.360            0.308000    0.500000       0.978   
2  ...                  0.392            0.337333    0.352667       0.689   
3  ...                  0.500            0.359000    0.486000       0.962   
4  ...                  0.000            0.288000    0.496000       1.000   

   Dunks %FGA  # of Dunks Corner 3s %3PA Corner 3s 3P% Attempted Heaves  \
0    0.039000           7       0.456000      0.258000                1   
1    0.017000           8       0.390000      0.333000                3   
2    0.011667           5       0.158667      0.308000                5   
3    0.014000          19       0.091000      0.350000                1   
4    0.030333           2       0.485667      0.317667                0   

   # of Heaves  
0            0  
1            0  
2            0  
3            0  
4            0  

[5 rows x 59 columns]

In [3]:
data['college'].value_counts()

None                                  567
Kentucky                              215
Duke                                  193
UCLA                                  165
Arizona                               142
                                     ... 
California-Los Angeles                  1
University of California, Berkeley      1
Marshall                                1
Alabama-Birmingham                      1
Montana State                           1
Name: college, Length: 220, dtype: int64

In [4]:
acc = ['Boston College', 'Clemson', 'Duke', 'Georgia Tech', 'Florida State', 'North Carolina', 'Syracuse', 'Louisville', 
       'Miami', 'North Carolina State', 'Notre Dame', 'Pittsburgh', 'Virginia', 'Wake Forest']
sec = ['Alabama', 'Arkansas', 'Florida', 'Georgia', 'Kentucky', 'LSU', 'Mississippi', 'Missouri', 'South Carolina',
       'Tennessee', 'Texas A&M', 'Vanderbilt']
big12 = ['Baylor', 'Texas', 'Oklahoma', 'Iowa State', 'Kansas', 'Kansas State', 'Oklahoma State', 'TCU', 'Texas Tech', 
         'West Virginia']
big10 = ['Illinois', 'Indiana', 'Iowa', 'Maryland', 'Michigan', 'Michigan State', 'Minnesota', 'Nebraska', 'Northwestern', 
         'Ohio State', 'Penn State', 'Purdue', 'Rutgers', 'Wisconsin']
pac12 = ['UCLA', 'Arizona', 'USC', 'Oregon', 'Arizona State', 'Washington State', 'Utah', 'Colorado', 'Washington', 
         'California', 'Stanford', 'Oregon State']
bigeast = ['Marquette', 'Xavier', 'Creighton', 'Conneticut', 'Providence', 'Seton Hall', 'Villanova', "St John's", 'DePaul',
           'Butler', 'Georgetown']

In [5]:
conf = []
for row in data['college']:
    if row in acc:
        conf.append("ACC")
    elif row in sec:
        conf.append("SEC")
    elif row in big12:
        conf.append("BIG-12")
    elif row in big10:
        conf.append("BIG-10")
    elif row in pac12:
        conf.append("PAC-12")
    elif row in bigeast:
        conf.append("BIG-EAST")
    else:
        conf.append("OTHER")

In [6]:
data['conf'] = conf
data['conf'].value_counts()

OTHER       1713
ACC          771
PAC-12       632
SEC          556
BIG-10       417
BIG-12       383
BIG-EAST     294
Name: conf, dtype: int64

In [7]:
first_round = list(range(1,31))
first_round_str = []
for i in first_round:
    first_round_str.append(str(i))

In [8]:
first = data[data['draft_number'].isin(first_round_str)]

In [9]:
pick_conf_heatmap = alt.Chart(first, title = "Draft Pick Number for College Conference").mark_rect().encode(
    alt.X("conf:N", axis = alt.Axis(title = "College Conference")), 
    alt.Y("draft_number:O", axis = alt.Axis(title = "Draft Pick #"), scale = alt.Scale(domain = first_round_str)), 
    alt.Color("count():Q"),
    alt.Tooltip("count():Q")
).properties(
    width = 200,
    height = 400
)
pick_conf_hist = alt.Chart(first, title = "Frequency of Draft Picks with College Conference").mark_bar().encode(
    alt.X("draft_number:O", scale = alt.Scale(domain = first_round_str), axis = alt.Axis(title = "Draft Pick #")), 
    alt.Y("count():Q"), 
    alt.Color("conf:N", legend=alt.Legend(title="College Conference")), 
    alt.Tooltip("count():N")
).properties(width = 460)
pick_conf_heatmap | pick_conf_hist

/Applications/miniconda3/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.HConcatChart(...)

In [10]:
import ast
def convert_to_list(x):
    if not isinstance(x, list):
        return [x]
    else:
        return x
data['positions'] = data['positions'].apply(convert_to_list)

def remove_extra_brackets(x):
    if len(x[0]) > 20:
        txt = x[0].replace("['", "['").replace("' '", "', '")
        return ast.literal_eval(txt)
    return x
data['positions'] = data['positions'].apply(remove_extra_brackets)

def convert_from_list(x):
    if isinstance(x, list):
        return x[0]
    else:
        return x
data['team'] = data['team'].apply(convert_from_list)

data_boom = data.explode('positions')
data['team'] = data['team'].apply(convert_from_list)

In [11]:
pos = data_boom['positions'].unique().tolist()
data['positions'] = data['positions'].apply(convert_from_list)

In [20]:
data_teams = data[data['team'].isin(["BOSTON CELTICS", "MIAMI HEAT", "NEW YORK KNICKS"])]
data_teams['positions'].value_counts()

SHOOTING GUARD    105
POINT GUARD       100
SMALL FORWARD      84
POWER FORWARD      77
CENTER             42
Name: positions, dtype: int64

In [21]:
click = alt.selection_multi(fields = ['team'], on = 'mouseover')
positions = ["POINT GUARD", "SHOOTING GUARD", "SMALL FORWARD", "POWER FORWARD", "CENTER"]
selectPos = alt.selection_single(
    name = 'Select', 
    fields=['positions'],
    bind=alt.binding_select(options=positions)
)


base = alt.Chart(data_teams, title = "3PT % vs # of Dunks over Time").encode(
    alt.X("Year:O")
)

line1 = base.mark_line(strokeWidth = 5).encode(
    alt.Y("average(FG% by Distance 3P)", axis = alt.Axis(title = "Average 3P% (marked by thicker line)")), 
    alt.Color("team:N"), 
    alt.Tooltip("average(FG% by Distance 3P)"),
    opacity = alt.condition(click, alt.value(1), alt.value(0.2))
)

line2 = base.mark_line(point = True).encode(
    alt.Y("average(# of Dunks)", axis = alt.Axis(title = "Average # of Dunks (marked by line with points)")), 
    alt.Color("team:N"), 
    alt.Tooltip("average(# of Dunks)"),
    opacity = alt.condition(click, alt.value(1), alt.value(0.2)), 
)
full_line = alt.layer(line1, line2).resolve_scale(
    y = 'independent'
).add_selection(selectPos).transform_filter(selectPos).properties(
    height = 400, 
    width = 400).interactive()

bar = alt.Chart(
    data_teams, 
    title = "Average of # of Dunks and 3PT % by Team"
).transform_fold(
    ['# of Dunks', 'FG% by Distance 3P'],
    ['type', 'value'],
).mark_bar().encode(
    column='type:N',
    x='team:N',
    y='average(value):Q',
    color = alt.Color("team:N"),
    opacity = alt.condition(click, alt.value(1), alt.value(0.2))
).properties(
    width=100
).resolve_scale(
    y = 'independent'
).add_selection(selectPos).transform_filter(selectPos).interactive()

full_view = alt.hconcat(full_line.add_selection(click), bar.add_selection(click)).configure_point(size = 100)
full_view

/Applications/miniconda3/lib/python3.10/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.HConcatChart(...)